## Use the Gaussian Error-Function as the model

In [480]:
import sys
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
from matplotlib import ticker
from matplotlib.dates import (DateFormatter, drange)
import seaborn as sns
import datetime
from scipy import interpolate
from scipy.optimize import curve_fit


from scipy.integrate import odeint 
from scipy.integrate import solve_ivp

from scipy.fft import fft 

from IPython.core.display import display, HTML

import geopandas as gpd
import seaborn as sns

In [481]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
from plotly.subplots import make_subplots

import cufflinks as cf
%matplotlib inline 
init_notebook_mode(connected=True)
cf.go_offline()

# pd.set_option('display.max_columns', None)
# pd.set_option("display.max_rows", None)


In [482]:
pd.set_option('display.max_columns', 10)
pd.set_option("display.max_rows", 10)



## Define the Data-Set

In [483]:
covid19   = "https://opendata.arcgis.com/datasets/dd4580c810204019a7b8eb3e0b329dd6_0.geojson"
url = covid19
df = gpd.read_file(url, orient='columns', lines=True)
#print(df.info())

u = df.groupby('Meldedatum', as_index=False).sum()
u.drop(['FID', 'IdBundesland', 'AnzahlFall', 
       'NeuerFall', 'NeuerTodesfall', 'NeuGenesen','IstErkrankungsbeginn'],
       axis=1, inplace=True)

y = df.groupby('Refdatum', as_index=False).sum()
y.drop(['FID', 'IdBundesland', 'NeuerFall', 'NeuerTodesfall', 'NeuGenesen', 
        'AnzahlGenesen','AnzahlTodesfall','IstErkrankungsbeginn'],
#y.drop(['FID', 'IdBundesland', 'IstErkrankungsbeginn'],
       axis=1, inplace=True)

In [484]:
yu = y.merge(u, left_on='Refdatum', right_on='Meldedatum', how='left')
yu.drop(['Meldedatum'], axis=1, inplace=True)
yu.loc[yu['AnzahlGenesen'].isna(), 'AnzahlGenesen'] = 0
yu

Refdatum  AnzahlFall  AnzahlTodesfall  AnzahlGenesen
0    2020-01-01T00:00:00           1              NaN            0.0
1    2020-01-02T00:00:00           1              NaN            0.0
2    2020-01-06T00:00:00           1              NaN            0.0
3    2020-01-17T00:00:00           2              NaN            0.0
4    2020-01-20T00:00:00           1              NaN            0.0
..                   ...         ...              ...            ...
115  2020-05-13T00:00:00         593              9.0           52.0
116  2020-05-14T00:00:00         508              1.0           39.0
117  2020-05-15T00:00:00         414              3.0           11.0
118  2020-05-16T00:00:00         272              0.0            6.0
119  2020-05-17T00:00:00          94              0.0            2.0

[120 rows x 4 columns]

In [485]:

u

Meldedatum  AnzahlTodesfall  AnzahlGenesen
0   2020-01-28T00:00:00                0              4
1   2020-01-29T00:00:00                0              2
2   2020-01-31T00:00:00                0              3
3   2020-02-03T00:00:00                0              1
4   2020-02-04T00:00:00                0              4
..                  ...              ...            ...
90  2020-05-13T00:00:00                9             52
91  2020-05-14T00:00:00                1             39
92  2020-05-15T00:00:00                3             11
93  2020-05-16T00:00:00                0              6
94  2020-05-17T00:00:00                0              2

[95 rows x 3 columns]

In [486]:
x  = pd.to_datetime(yu[:]['Refdatum'])
t0 = datetime.datetime(2020,1,1)
xe = x - t0
xe = xe.dt.days
xe = xe.rename("Elapsed Day")

In [487]:
df1 = pd.DataFrame(xe.to_numpy(), columns=['Elapsed Day'])
df1['Date'] = x
df1['Daily Infection'] = yu['AnzahlFall']
df1['Daily Exit'] = yu['AnzahlTodesfall'] +  yu['AnzahlGenesen']
# df1['Daily Exit Rewind'] = y['AnzahlTodesfall'] +  y['AnzahlGenesen']
df1['Cumulative Infection'] = df1['Daily Infection'].cumsum()
df1['Cumulative Exit'] = df1['Daily Exit'].cumsum()
# df1['Cumulative Exit Rewind'] = df1['Daily Exit Rewind'].cumsum()
df1
# y.drop(['AnzahlGenesen', 'AnzahlDodesfall'], axis=1, inplace=True)


Elapsed Day       Date  Daily Infection  Daily Exit  \
0              0 2020-01-01                1         NaN   
1              1 2020-01-02                1         NaN   
2              5 2020-01-06                1         NaN   
3             16 2020-01-17                2         NaN   
4             19 2020-01-20                1         NaN   
..           ...        ...              ...         ...   
115          133 2020-05-13              593        61.0   
116          134 2020-05-14              508        40.0   
117          135 2020-05-15              414        14.0   
118          136 2020-05-16              272         6.0   
119          137 2020-05-17               94         2.0   

     Cumulative Infection  Cumulative Exit  
0                       1              NaN  
1                       2              NaN  
2                       3              NaN  
3                       5              NaN  
4                       6              NaN  
..                    ...              ...  
115                173399         162417.0  
116                173907         162457.0  
117                174321         162471.0  
118                174593         162477.0  
119                174687         162479.0  

[120 rows x 6 columns]

## Daily Infection

In [488]:
f = go.Figure()
f.add_trace(go.Bar(x=df1['Date'], y=df1['Daily Infection'], name='Daily Infection'))
#                       mode='markers', name='Infected', 
#                       marker=dict(symbol="circle", size=8,
#                                   line=dict(width=1, color='white'))))

f.add_trace(go.Scatter(x=df1['Date'], y=df1['Daily Exit'],
                        mode='lines', name='Recovered'))

# f.add_trace(go.Scatter(x=df1['Date'], y=df1['Daily Exit Rewind'],
#                         mode='lines', name='Recovered Rewind'))

# f.update_layout(yaxis_type="log", template='ggplot2')
f.update_layout(template='ggplot2')
f.show()

In [489]:
f = go.Figure()
f.add_trace(go.Scatter(x=df1['Date'], y=df1['Cumulative Infection'],
                       mode='markers', name='Infected', 
                       marker=dict(symbol="circle", size=8,
                                   line=dict(width=1, color='white'))))

f.add_trace(go.Scatter(x=df1['Date'], y=df1['Cumulative Exit'], 
                       mode='lines', name='Recovered'))
# f.update_layout(yaxis_type="log", template='ggplot2')
f.update_layout(template='ggplot2')
f.show()

## Remove Weekly Trend

In [490]:
dfw = df1.copy()

In [491]:
# from folowoing date, sampling is continuous
ix = max(xe[xe - np.roll(xe, 1) !=1])
t1 = dfw['Date'][:].dt.day_name()    
dfw['Day of Week'] = t1
t2 = dfw['Date'][:].dt.weekday
dfw['Weekday'] = t2
t3 = dfw['Date'][:].dt.weekofyear
dfw['Week of Year'] = t3
dfw.head(3)



Elapsed Day       Date  Daily Infection  Daily Exit  Cumulative Infection  \
0            0 2020-01-01                1         NaN                     1   
1            1 2020-01-02                1         NaN                     2   
2            5 2020-01-06                1         NaN                     3   

   Cumulative Exit Day of Week  Weekday  Week of Year  
0              NaN   Wednesday        2             1  
1              NaN    Thursday        3             1  
2              NaN      Monday        0             2

In [513]:
f= go.Figure()
# f.add_trace(go.Bar(x=df_week['Day of Week'], y=df_week['infected daily'], name='a'))

i_week = list(set(dfw['Week of Year']))
i_week = i_week[4:-1]

for i in i_week:
#    xx = df[df['Week of Year'] == i]['Day of Week']
    xx = dfw[dfw['Week of Year'] == i]['Weekday']
    yy = dfw[dfw['Week of Year'] == i]['Daily Infection']
#    print(xx)
#    f.add_trace(go.Bar(x=df['Week of Year'], y=df['Infected daily'], name='a'))
#    f.add_trace(go.Bar(x=xx, y=yy, name=i, opacity=0.5))
    f.add_trace(go.Bar(x=xx, y=yy, name=str(i) + ' Week of Y'))
                

#f.update_layout(
f.update_layout(template='ggplot2', barmode='stack', 
                xaxis = dict(tickvals = list(range(0,7)), 
                             ticktext = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 
                                         'Friday', 'Saturday', 'Sunday']))


f.show()
#-----------------------------------------------
dfw1 = dfw.copy()
dfw1 = dfw1[(dfw1['Week of Year'] >=5) &  (dfw1['Week of Year'] <=19) ][:]
# df1.info()
# df1.head(3)
dfw1 = dfw1.groupby('Weekday', as_index=False).sum()

ifk = dfw1['Daily Infection'] / dfw1['Daily Infection'].mean()
dfw1['Normalization factor'] = ifk

ifk2 = dfw1['Daily Exit'] / dfw1['Daily Exit'].mean()
dfw1['Normalization factor2'] = ifk2

# ifk3 = dfw1['Daily Exit Rewind'] / dfw1['Daily Exit Rewind'].mean()
# dfw1['Normalization factor3'] = ifk3


df3 = dfw1.copy()
df3.info()

# df3.drop(['Elapsed Day', 'Daily Infection', 'Daily Exit', 'Daily Exit Rewind',
#           'Cumulative Infection', 'Cumulative Exit', 'Cumulative Exit Rewind', 
#           'Week of Year'], 
#           axis=1, inplace=True)

df3.drop(['Elapsed Day', 'Daily Infection', 'Daily Exit', 
          'Cumulative Infection', 'Cumulative Exit', 
          'Week of Year'], 
           axis=1, inplace=True)


# df3 = df3.drop('Infected daily', axis=1)
df3.head(3)
df4 = pd.merge(dfw, df3, on='Weekday')
# df4['Modified Daily Infection'] = df4['Infected daily'] * 2
df4['MDI'] = df4['Daily Infection'] / df4['Normalization factor'] 
df4['MDR'] = df4['Daily Exit'] / df4['Normalization factor2'] 
# df4['MDRRW'] = df4['Daily Exit Rewind'] / df4['Normalization factor3'] 


df4 = df4.sort_values(by='Date')
df4 = df4.reset_index()

df4['MCI'] = df4['MDI'].cumsum()
df4['MCR'] = df4['MDR'].cumsum()


#-----------------------------------------------
# plot
#-----------------------------------------------
f= go.Figure()
f.add_trace(go.Bar(x=dfw1['Weekday'], y=dfw1['Daily Infection']))

f.update_layout(template='ggplot2', barmode='stack', 
                xaxis = dict(tickvals = list(range(0,7)), 
                             ticktext = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 
                                         'Friday', 'Saturday', 'Sunday']))

f.show()
#-----------------------------------------------
# Infection Before / After
# f= go.Figure()
f = make_subplots(rows=2, cols=1)

f.append_trace(go.Bar(x=df4['Date'], y=df4['Daily Infection'], name='Before'), 
               row=1, col=1)
f.append_trace(go.Bar(x=df4['Date'], y=df4['MDI'], name='After'), row=2, col=1)

f.update_layout(template='ggplot2', barmode='overlay')

f.update_xaxes(range=('2020-02-16','2020-05-20'))
f.show()

#-----------------------------------------------
# Recovery Before / After
# f= go.Figure()
f = make_subplots(rows=2, cols=1)

f.append_trace(go.Bar(x=df4['Date'], y=df4['Daily Exit'], name='Before'), 
               row=1, col=1)
f.append_trace(go.Bar(x=df4['Date'], y=df4['MDR'], name='After'), row=2, col=1)

f.update_layout(template='ggplot2', barmode='overlay')

f.update_xaxes(range=('2020-02-16','2020-05-20'))
f.show()
#-----------------------------------------------
# Recovery Before / After Rewind
# f= go.Figure()
# f = make_subplots(rows=2, cols=1)

# f.append_trace(go.Bar(x=df4['Date'], y=df4['Daily Exit Rewind'], name='Before'), 
#               row=1, col=1)
# f.append_trace(go.Bar(x=df4['Date'], y=df4['MDRRW'], name='After'), row=2, col=1)

# f.update_layout(template='ggplot2', barmode='overlay')

# f.update_xaxes(range=('2020-02-16','2020-05-20'))
# f.show()




#-----------------------------------------------
#-----------------------------------------------
# infection

f= go.Figure()
# f.add_trace(go.Bar(x=df_week['Day of Week'], y=df_week['infected daily'], name='a'))

i_week = list(set(dfw['Weekday']))

for i in i_week:
#    xx = df[df['Week of Year'] == i]['Day of Week']
    xx = dfw[(dfw['Weekday'] == i) & (dfw['Week of Year'] > 12)]['Week of Year']
    yy = dfw[(dfw['Weekday'] == i) & (dfw['Week of Year'] > 12)]['Daily Infection']

    #    f.add_trace(go.Bar(x=df['Week of Year'], y=df['Infected daily'], name='a'))
#    f.add_trace(go.Bar(x=xx, y=yy, name=i, opacity=0.5))
    f.add_trace(go.Bar(x=xx, y=yy))

#f.update_layout(
f.update_layout(template='ggplot2', barmode='group')
f.show()

#-----------------------------------------------
#-----------------------------------------------
# Recovery

f= go.Figure()
# f.add_trace(go.Bar(x=df_week['Day of Week'], y=df_week['infected daily'], name='a'))

i_week = list(set(dfw['Weekday']))

for i in i_week:
#    xx = df[df['Week of Year'] == i]['Day of Week']
    xx = dfw[(dfw['Weekday'] == i) & (dfw['Week of Year'] > 12)]['Week of Year']
    yy = dfw[(dfw['Weekday'] == i) & (dfw['Week of Year'] > 12)]['Daily Exit']

    #    f.add_trace(go.Bar(x=df['Week of Year'], y=df['Infected daily'], name='a'))
#    f.add_trace(go.Bar(x=xx, y=yy, name=i, opacity=0.5))
    f.add_trace(go.Bar(x=xx, y=yy))

#f.update_layout(
f.update_layout(template='ggplot2', barmode='group')
f.show()

#-----------------------------------------------
#-----------------------------------------------
# Recovery Rewind

# f= go.Figure()
# f.add_trace(go.Bar(x=df_week['Day of Week'], y=df_week['infected daily'], name='a'))

# i_week = list(set(dfw['Weekday']))

# for i in i_week:
#    xx = df[df['Week of Year'] == i]['Day of Week']
#     xx = dfw[(dfw['Weekday'] == i) & (dfw['Week of Year'] > 12)]['Week of Year']
#     yy = dfw[(dfw['Weekday'] == i) & (dfw['Week of Year'] > 12)]['Daily Exit Rewind']

    #    f.add_trace(go.Bar(x=df['Week of Year'], y=df['Infected daily'], name='a'))
#    f.add_trace(go.Bar(x=xx, y=yy, name=i, opacity=0.5))
#     f.add_trace(go.Bar(x=xx, y=yy))

#f.update_layout(
# f.update_layout(template='ggplot2', barmode='group')
# f.show()







<class 'pandas.core.frame.DataFrame'>
Int64Index: 7 entries, 0 to 6
Data columns (total 9 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   Weekday                7 non-null      int64  
 1   Elapsed Day            7 non-null      int64  
 2   Daily Infection        7 non-null      int64  
 3   Daily Exit             7 non-null      float64
 4   Cumulative Infection   7 non-null      int64  
 5   Cumulative Exit        7 non-null      float64
 6   Week of Year           7 non-null      int64  
 7   Normalization factor   7 non-null      float64
 8   Normalization factor2  7 non-null      float64
dtypes: float64(4), int64(5)
memory usage: 560.0 bytes


## SIR model

In [514]:
def sir_prot(z,t,be): # t is tau (unit of 1/re)

    s = z[0]
    i = z[1]
    r = z[2]
    
#    re = 1.0/1.0 # 3 weeks
#    tr =  re * R_0 / n0 / s
#    print(tr, R_0, n0)

    dsdt = -be / re * s * i
    didt =  be / re * s * i - i
    drdt =  i
    
    dzdt = [dsdt,didt,drdt]
    return dzdt

#--------------------------------------------------------------------
# initial condition. All fractional 

# n0 = 2e5  # germany
re = 1.0/21.0 # 3 weeks
# re = 1.0/14.0 # 2 weeks
# re = 1.0/28.0 # 4 weeks

i0 = 1e-6
s0 = 1.0-i0
r0 = 0.00

z0 = [s0,i0,r0]

# time points
# n = 10 # ncycle
# t = np.arange(0,n, 0.1)  
n  = 1001
td = np.linspace(0,n-1,num=n) # days

# solve ODE
R0 = 3.0
be = R0 * re
# tr = re * R_0 / n0 / s0
z = odeint(sir_prot, z0, td * re, args=(be,))


In [515]:
R0s = np.arange(4, 0.5, -0.1)
bes = R0s * re

In [516]:
# Create figure
f = go.Figure()
trace1=[]
trace2=[]
trace3=[]

# Add traces, one for each slider step
for be in bes:
    z = odeint(sir_prot, z0, td * re, args=(be,))
    trace1.append(dict(type='scatter', mode='lines', 
                       visible=False, name='Susceptible', x=td, y=z[:,0]))

    trace2.append(dict(type='scatter', mode='lines', 
                       visible=False, name='Infected', x=td, y=z[:,1]))
    
    trace3.append(dict(type='scatter', mode='lines', 
                       visible=False, name='Recovered', x=td, y=z[:,2]))

all_trace = trace1 + trace2 + trace3
nb = len(bes) # number of model
# np = len(all_trace) / len(trs)
# all_trace = [trace1, trace2, trace3]


In [517]:
f = go.Figure(data=all_trace)
# Make 10th trace visible


In [497]:
# Create and add slider
models = []
# for i in range(len(f.data)):
for i in range(nb):
    mo = dict(
        method='update',
        args=[{'visible': [False] * len(f.data)},
              {'title': 'Reproduction Number ' + str(np.around(R0s[i], 1))  }], 
        label=str(np.around(R0s[i], 1))
    )
    
        # layout attribute
    mo['args'][0]['visible'][i]   = True  # Toggle i'th trace to "visible"
    mo['args'][0]['visible'][i+nb] = True  # Toggle i'th trace to "visible"
    mo['args'][0]['visible'][i+nb+nb] = True  # Toggle i'th trace to "visible"
    models.append(mo)

sliders = [dict(
    currentvalue = dict(visible=False),
    pad = dict(t=32),
    minorticklen=0,
    steps = models
)]

f.update_layout(
    template = 'ggplot2', 
    sliders  = sliders
)
#f.show()
# ago.FigureWidget(f)

## SIR cumulative model -- Before Lockdown


In [531]:
i0 = 1e-4
s0 = 1.0-i0
r0 = 0.00
z0 = [s0,i0,r0]

# solve ODE
R0 = 3.0


In [532]:
def sir_cumulative(x,a,b,R0):

    be = R0 * re
    x = np.insert(x,0,0) 
    t = x - a  # put 0 at index=0

    z = odeint(sir_prot, z0, t*re, args=(be,))
    z = np.delete(z, 0, axis=0)

    cum = b * (z[:,1] + z[:,2])
    return cum



In [533]:
df5 = df4.copy()


In [534]:
cf, cov = curve_fit(sir_cumulative, 
                    df5['Elapsed Day'].to_numpy(),
                    df5['MCI'].to_numpy(),
                    bounds=([-120, 0, 0],
                            [120, 1e6,10]),  
                    p0=[0, 2e5, 3.0]
                   )
df5['CI SIR'] = sir_cumulative(xe.to_numpy(), *cf)
df5['DI SIR'] = df5['CI SIR'] - np.roll(df5['CI SIR'], 1)
cf

array([9.48914032e+01, 1.93864052e+05, 3.08738267e+00])

In [536]:
f = go.Figure()
f.add_trace(go.Scatter(x=df5['Date'], y=df5['MCI'], 
                       mode='markers', name='Infected', 
                       marker=dict(symbol="circle", size=8,
                                   line=dict(width=1, color='white'))))

f.add_trace(go.Scatter(x=df5['Date'], y=df5['CI SIR'], 
                       mode='lines', name='SIR model'))
# f.update_layout(yaxis_type="log", template='ggplot2')
f.update_layout(template='ggplot2')
f.show()

In [569]:
df5['Date']
i0 = 1e-7
s0 = 1.0-i0
r0 = 0.00
z0 = [s0,i0,r0]

# solve ODE
R0 = 3.0



In [570]:
t_ld = pd.Timestamp(2020,3,20)
t_ld
xx = df5[df5['Date'] <= t_ld]['Elapsed Day']
xt = df5[df5['Date'] <= t_ld]['Date']
yy = df5[df5['Date'] <= t_ld]['MCI']

cf, cov = curve_fit(sir_cumulative, 
                    xx.to_numpy(),
                    yy.to_numpy(),
                    bounds=([-1000, 0, 0],
                            [1000, 1e6,10]),  
                    p0=[0, 1e6, 5.0]
                   )
df5['CI SIR BLR'] = sir_cumulative(xe.to_numpy(), *cf)
df5['DI SIR BLR'] = df5['CI SIR BLR'] - np.roll(df5['CI SIR BLR'], 1)
cf

array([-2.34592580e+02,  7.98102782e+05,  4.50389398e+00])

In [571]:
f = go.Figure()
f.add_trace(go.Scatter(x=df5['Date'], y=df5['MCI'], 
                       mode='markers', name='Infected', 
                       marker=dict(symbol="circle", size=8,
                                   line=dict(width=1, color='white'))))
f.add_trace(go.Scatter(x=xt, y=yy, 
                       mode='markers', name='Infected', 
                       marker=dict(symbol="circle", size=8,
                                   line=dict(width=1, color='white'))))

f.add_trace(go.Scatter(x=df5['Date'], y=df5['CI SIR BLR'], 
                       mode='lines', name='SIR model'))
# f.update_layout(yaxis_type="log", template='ggplot2')
f.update_layout(template='ggplot2')
f.show()

## Recovery



In [572]:
f = go.Figure()
f.add_trace(go.Bar(x=df5['Date'], y=df5['MCI'], name='MCI'))
f.add_trace(go.Bar(x=df5['Date'], y=df5['MCR'], name='MCR', opacity=0.7))

# f.update_xaxes(range=('2020-01-01','2020-05-20'))
f.update_xaxes(range=('2020-02-20',pd.Timestamp.today()))
# f.update_yaxes(range=(0,6e3))
f.update_layout(template='ggplot2', barmode='overlay')
f.show()

f = go.Figure()
f.add_trace(go.Bar(x=df5['Date'], y=df5['MDI'], name='MDI'))
f.add_trace(go.Bar(x=df5['Date'],
                   y=df5['MDR'], name='MDR', opacity=0.5))

f.add_trace(go.Bar(x=df5['Date']-datetime.timedelta(days=5), 
                   y=df5['MDR'], name='offset', opacity=0.5))


# f.update_xaxes(range=('2020-01-01','2020-05-20'))
f.update_xaxes(range=('2020-02-20',pd.Timestamp.today()))
# f.update_yaxes(range=(0,6e3))
f.update_layout(template='ggplot2', barmode='overlay')
f.show()





In [573]:
f = go.Figure()
f.add_trace(go.Bar(x=df5['Date'], y=df5['MCI'], name='MCI'))
f.add_trace(go.Bar(x=df5['Date'], y=df5['MCI']-df5['MCR'], name='MCI', opacity=0.7))

# f.update_xaxes(range=('2020-01-01','2020-05-20'))
f.update_xaxes(range=('2020-02-20',pd.Timestamp.today()))
# f.update_yaxes(range=(0,6e3))
f.update_layout(template='ggplot2', barmode='overlay')
f.show()



## Basic Reproduction Number



In [574]:
t0 = pd.Timestamp.today() - datetime.timedelta(days=14)
t0

Timestamp('2020-05-04 11:00:10.828994')

In [575]:
f = go.Figure()

f.add_trace(go.Scatter(x=df5[df5['Date'] <= t0]['Date'], 
                       y=df5[df5['Date'] <= t0]['MDI']/df5[df5['Date']<= t0]['MDR'], 
                       mode='lines', name='R0'))


# f.add_trace(go.Scatter(x=df5['Date'], y=df5['MDI']/df5['MDRRW'], 
#                        mode='lines', name='Rewind'))


f.update_xaxes(range=('2020-01-20',pd.Timestamp.today()))
# f.update_yaxes(range=(-0.3,1))
# f.update_layout(yaxis_type="log", template='ggplot2')
f.update_yaxes(range=(0,10))
f.update_layout(template='ggplot2')
f.show()

